In [75]:
import time
import threading

# Threading Exercises

1. Write a Python program to create multiple threads and print their names.
2. Write a Python program to download multiple files concurrently using threads.
3. Write a Python program that creates two threads to find and print even and odd numbers from 30 to 50.
4. Write a Python program to calculate the factorial of a number using multiple threads.
5. Write a Python program that performs concurrent HTTP requests using threads.

In this notebook, I propose solutions to the previously mentioned questions using the threading module. Our goal is to harness the benefits of concurrent programming. Threads allow for the execution of multiple tasks simultaneously, which reduces the solution time compared to a synchronous programming paradigm.

## Solution Exercise 1
In synchronous programming that utilizes a single thread (the main thread) and when we want to simulate different threads on each iteration, we can use the following program to solve the problem:

In [74]:
number_threads = 10 # Number of threads.

def thread_name(threading_number: int) -> None:
    '''
    This function provides the name of the thread
    used to perform some transformation.
    '''
    time.sleep(10) # It simulates a difficult task that requires 1 sec to finish.
    print(f'Threading_{threading_number}')

initial_time = time.time()

for i in range(number_threads):
    thread_name(i)

final_time = time.time()
print(f'\nTime elapsed: {final_time - initial_time}')

Threading_0
Threading_1
Threading_2
Threading_3
Threading_4
Threading_5
Threading_6
Threading_7
Threading_8
Threading_9

Time elapsed: 100.00578331947327


As you can see, the time elapsed for this type of sequential programming is $t=100$ seconds. However, using actual threading, this time is significantly reduced.

In [76]:
threads = [] # list of threads.

initial_time = time.time()

for i in range(number_threads):
    t = threading.Thread(target = thread_name, args = (i,))
    threads.append(t)
    t.start() # It initializes the threads.

for t in threads:
    t.join() # The main program continues when the threads have completed their tasks.

final_time = time.time()
print(f'\nTime elapsed: {final_time - initial_time}')

Threading_0Threading_4
Threading_3
Threading_2
Threading_1
Threading_6
Threading_7
Threading_5
Threading_9

Threading_8

Time elapsed: 10.003375768661499


**Conclusion**: We can perform multiple tasks simultaneously using threading instead of the traditional programming approach.

## Solution Excercise 2

In this excercise I will simulate that a program download some file in a random. To do that I will use the libraries random and time. 

In [52]:
def download_file(thread_name: int = None) -> None:
    print(f"Downloading file from URL_{thread_name}")
    time.sleep(10)
    print(f'Download finish by thread_{thread_name}!')

In [53]:
threads = []
number_connections = 10

for i in range(number_connections):
    t = threading.Thread(target = download_file, args = (i,))
    threads.append(t)
    t.start()

for t in threads:
    t.join()

Download finish by thread_0!
Download finish by thread_1!
Download finish by thread_2!
Download finish by thread_4!
Download finish by thread_8!
Download finish by thread_9!
Download finish by thread_6!
Download finish by thread_5!
Download finish by thread_7!
Download finish by thread_3!


In [54]:
# Excercise 3: 

numbers = [number for number in range(30, 50 + 1)]
print(numbers)

[30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50]


In [55]:
odd_list = []
even_list = []

def get_filter(number: int):
    global odd_list
    global even_list

    if number%2 == 0:
        even_list.append(number)
    else:
        odd_list.append(number)

In [56]:
threads = []

for number in numbers:
    t = threading.Thread(target = get_filter, args = (number,))
    threads.append(t)
    t.start()

for t in threads:
    t.join()

In [57]:
print(f'Odd list: {odd_list}')
print(f'Even list: {even_list}')

Odd list: [31, 33, 35, 37, 39, 41, 43, 45, 47, 49]
Even list: [30, 32, 34, 36, 38, 40, 42, 44, 46, 48, 50]


In [58]:
# Excercise 4: 

def get_partitions(num: int, partitions: int) -> dict:
    factorial_list = [number for number in range(1, num + 1)]

    lenght = int(len(factorial_list)/partitions)
    rest = len(factorial_list)%partitions

    partitions_dict = {}

    for i in range(lenght):
        partitions_dict[f'partitions_{i}'] = factorial_list[partitions*i : partitions*(i + 1)]

        if rest != 0 and i == lenght - 1:
            partitions_dict[f'partitions_{i + 1}'] = factorial_list[partitions*(i + 1) : ]

    return partitions_dict

In [59]:
number_partition = get_partitions(1000, 30)

In [60]:
from functools import reduce
import operator

def multiply_list(lst):
    return reduce(operator.mul, lst, 1)

In [61]:
rest_list = []
threads = []

def set_rest_list(lst):
    rest_list.append(multiply_list(lst))

partions_name = list(number_partition.keys())

for partion_name in partions_name:
    t = threading.Thread(target = set_rest_list, args = (number_partition[partion_name],))
    threads.append(t)
    t.start()

for t in threads:
    t.join()

print(multiply_list(rest_list))

4023872600770937735437024339230039857193748642107146325437999104299385123986290205920442084869694048004799886101971960586316668729948085589013238296699445909974245040870737599188236277271887325197795059509952761208749754624970436014182780946464962910563938874378864873371191810458257836478499770124766328898359557354325131853239584630755574091142624174743493475534286465766116677973966688202912073791438537195882498081268678383745597317461360853795345242215865932019280908782973084313928444032812315586110369768013573042161687476096758713483120254785893207671691324484262361314125087802080002616831510273418279777047846358681701643650241536913982812648102130927612448963599287051149649754199093422215668325720808213331861168115536158365469840467089756029009505376164758477284218896796462449451607653534081989013854424879849599533191017233555566021394503997362807501378376153071277619268490343526252000158885351473316117021039681759215109077880193931781141945452572238655414610628921879602238389714760

In [62]:
# Excercise 5: 

import logging
import requests
from bs4 import BeautifulSoup

urls = {'New York Times': 'https://www.nytimes.com/international/',
        'BBC': 'https://www.bbc.com/news/topics/cyd7z4rvdm3t',
        'CoinDesk': 'https://www.coindesk.com/'}

In [63]:
def get_url_response(url: str):
    try:
        response = requests.get(url)
        html = response.text
        soup = BeautifulSoup(html, 'html.parser')
        return soup
    except Exception as e:
        logging.error(str(e))
        return

In [64]:
soup = get_url_response(urls['BBC'])
soup

<!DOCTYPE html>
<html class="no-js" lang="en-GB"><head><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1" name="viewport"/><title data-rh="true">Cryptocurrency - BBC News</title><meta content="All the latest content about Cryptocurrency from the BBC." data-rh="true" name="description"/><meta content="#FFFFFF" data-rh="true" name="theme-color"/><meta content="100004154058350" data-rh="true" property="fb:admins"/><meta content="All the latest content about Cryptocurrency from the BBC." data-rh="true" property="og:description"/><meta content="https://www.bbc.co.uk/news/special/2015/newsspec_10857/bbc_news_logo.png" data-rh="true" property="og:image"/><meta content="Logo for BBC News" data-rh="true" property="og:image:alt"/><meta content="BBC News" data-rh="true" property="og:site_name"/><meta content="Cryptocurrency - BBC News" data-rh="true" property="og:title"/><meta content="website" data-rh="true" property="og:type"/><meta content="https://www.bbc.com/news/topi

In [65]:
soups = {}

def set_soups(webpage_name: str) -> None:
    global soups
    soups[webpage_name] = get_url_response(urls[webpage_name])

webpages_name = list(urls.keys())
threads = []

for webpage_name in webpages_name:
    t = threading.Thread(target = set_soups, args = (webpage_name,))
    threads.append(t)
    t.start()

for t in threads:
    t.join()

In [68]:
soups['New York Times']

<!DOCTYPE html>

<html class="nytapp-vi-homepage" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<meta charset="utf-8"/>
<title data-rh="true">The New York Times International - Breaking News, US News, World News, Videos</title>
<meta content="The New York Times seeks the truth and helps people understand the world. With 1,700 journalists reporting from more than 150 countries, we provide live updates, investigations, photos and video of international and regional news, politics, business, technology, science, health, arts, sports and opinion." data-rh="true" name="description"/><meta content="https://www.nytimes.com/international/" data-rh="true" property="og:url"/><meta content="website" data-rh="true" property="og:type"/><meta content="The New York Times International - Breaking News, US News, World News, Videos" data-rh="true" property="og:title"/><meta content="The New York Times seeks the truth and helps people understand the world. With 1,700 journalists repor

In [70]:
soups['BBC']

<!DOCTYPE html>
<html class="no-js" lang="en-GB"><head><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1" name="viewport"/><title data-rh="true">Cryptocurrency - BBC News</title><meta content="All the latest content about Cryptocurrency from the BBC." data-rh="true" name="description"/><meta content="#FFFFFF" data-rh="true" name="theme-color"/><meta content="100004154058350" data-rh="true" property="fb:admins"/><meta content="All the latest content about Cryptocurrency from the BBC." data-rh="true" property="og:description"/><meta content="https://www.bbc.co.uk/news/special/2015/newsspec_10857/bbc_news_logo.png" data-rh="true" property="og:image"/><meta content="Logo for BBC News" data-rh="true" property="og:image:alt"/><meta content="BBC News" data-rh="true" property="og:site_name"/><meta content="Cryptocurrency - BBC News" data-rh="true" property="og:title"/><meta content="website" data-rh="true" property="og:type"/><meta content="https://www.bbc.com/news/topi

In [71]:
soups['CoinDesk']

<!DOCTYPE html>
<html lang="en"><head><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1" name="viewport"/><script>APP_ENV = "production";</script><script data-cookieconsent="ignore">window.dataLayer = window.dataLayer || [{"app_name":"arc","app_env":"production","app_version":"3.68.1","event":"page_view","media_type":"html","page_category":"homepage","page_url":"/homepage","page_pathname":"/","sponsored":false,"video_provider":"No Player Detected"}];function gtag() {window.dataLayer.push(arguments);}gtag("consent", "default", {ad_storage: "granted",analytics_storage: "granted",functionality_storage: "granted",personalization_storage: "granted",security_storage: "granted",wait_for_update: 500});gtag("set", "ads_data_redaction", false);gtag("set", "url_passthrough", true);gtag("consent", "default", {ad_storage: "denied",analytics_storage: "denied",functionality_storage: "granted",personalization_storage: "denied",security_storage: "granted",wait_for_update: 500,re